In [1]:
import tensorflow as tf

In [4]:
import numpy as np

In [8]:
def cnn_model_fn(features, labels, mode):
    """Model function for CNN."""
    # Input Layer
    input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])

    # Convolutional Layer #1
    conv1 = tf.layers.conv2d(
        inputs=input_layer,
        filters=32,
        kernel_size=[5, 5],
        padding="same",
        activation=tf.nn.relu)

    # Pooling Layer #1
    pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)

    # Convolutional Layer #2 and Pooling Layer #2
    conv2 = tf.layers.conv2d(
        inputs=pool1,
        filters=64,
        kernel_size=[5, 5],
        padding="same",
        activation=tf.nn.relu)
    pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)

    # Dense Layer
    pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])
    dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)
    dropout = tf.layers.dropout(inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)

    # Logits Layer
    logits = tf.layers.dense(inputs=dropout, units=10)

    predictions = {
        # Generate predictions (for PREDICT and EVAL mode)
        "classes": tf.argmax(input=logits, axis=1),
        # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
        # `logging_hook`.
        "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
    }

    if mode == tf.estimator.ModeKeys.PREDICT:
        return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

    # Calculate Loss (for both TRAIN and EVAL modes)
    loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)

    # Configure the Training Op (for TRAIN mode)
    if mode == tf.estimator.ModeKeys.TRAIN:
        optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
        train_op = optimizer.minimize(loss=loss, global_step=tf.train.get_global_step())
        return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)

    # Add evaluation metrics (for EVAL mode)
    eval_metric_ops = { "accuracy": tf.metrics.accuracy(labels=labels, predictions=predictions["classes"]) }
    return tf.estimator.EstimatorSpec(mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)

In [9]:
# Load training and eval data
mnist = tf.contrib.learn.datasets.load_dataset("mnist")
train_data = mnist.train.images # Returns np.array
train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
eval_data = mnist.test.images # Returns np.array
eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)

Successfully downloaded train-images-idx3-ubyte.gz 9912422 bytes.
Extracting MNIST-data/train-images-idx3-ubyte.gz
Successfully downloaded train-labels-idx1-ubyte.gz 28881 bytes.
Extracting MNIST-data/train-labels-idx1-ubyte.gz
Successfully downloaded t10k-images-idx3-ubyte.gz 1648877 bytes.
Extracting MNIST-data/t10k-images-idx3-ubyte.gz
Successfully downloaded t10k-labels-idx1-ubyte.gz 4542 bytes.
Extracting MNIST-data/t10k-labels-idx1-ubyte.gz


In [17]:
mnist_classifier = tf.estimator.Estimator(model_fn=cnn_model_fn, model_dir="/tmp/mnist_convnet_model")

INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_model_dir': '/tmp/mnist_convnet_model', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': None, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x7fb02c081b00>, '_task_type': 'worker', '_task_id': 0, '_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}


In [18]:
tensors_to_log = {"probabilities": "softmax_tensor"}
logging_hook = tf.train.LoggingTensorHook(tensors=tensors_to_log, every_n_iter=50)

In [19]:
# Train the model
train_input_fn = tf.estimator.inputs.numpy_input_fn(
    x={"x": train_data},
    y=train_labels,
    batch_size=100,
    num_epochs=None,
    shuffle=True)
mnist_classifier.train(
    input_fn=train_input_fn,
    steps=20000,
    hooks=[logging_hook])

INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Saving checkpoints for 1 into /tmp/mnist_convnet_model/model.ckpt.
INFO:tensorflow:probabilities = [[0.10687103 0.10425769 0.09391622 0.11385056 0.09945783 0.09581816
  0.10310929 0.09850231 0.08952603 0.09469094]
 [0.09520154 0.12244343 0.09649077 0.11369071 0.08596613 0.09695274
  0.09089462 0.10247325 0.08613828 0.10974858]
 [0.0992208  0.10087874 0.09289081 0.10998919 0.0985245  0.09555622
  0.09636175 0.10948165 0.09429734 0.10279898]
 [0.09638181 0.10269513 0.10392543 0.10921307 0.09682348 0.10453252
  0.09145569 0.10730572 0.09038082 0.09728634]
 [0.08965974 0.10118444 0.09809293 0.10697845 0.10090021 0.0982852
  0.10057962 0.09855746 0.09580246 0.10995957]
 [0.08766354 0.11987129 0.091976   0.10684165 0.09895424 0.09724332
  0.10397798 0.09894736 0.09391723 0.10060736]
 [0.09109849 0.10831442 0.09253728 0.1094167  0.09805132 0.09790903
  0.10640677 0.10393494 0.08338765 0.10894345]
 [0.0952044  0.11697317 0.09059832 0.

INFO:tensorflow:loss = 2.295632, step = 1
INFO:tensorflow:probabilities = [[0.10135812 0.10015074 0.09471215 0.10709123 0.10015572 0.10057233
  0.09849583 0.09692484 0.09831745 0.10222159]
 [0.08917812 0.09781162 0.10701925 0.10251479 0.09650605 0.10220574
  0.10430218 0.12367742 0.08697072 0.08981407]
 [0.10219939 0.10756881 0.08703337 0.10932766 0.09432159 0.10274763
  0.10192914 0.10286248 0.09477547 0.09723448]
 [0.09734324 0.10826735 0.09769627 0.10221899 0.09219091 0.09952404
  0.10488115 0.10694122 0.08858956 0.10234721]
 [0.10525602 0.09514479 0.10444226 0.09684861 0.08927875 0.10818399
  0.09307953 0.10867669 0.09472347 0.10436594]
 [0.09191112 0.11053745 0.10249624 0.12147783 0.10238882 0.09591015
  0.08402881 0.09619823 0.08088445 0.11416693]
 [0.09794541 0.10497373 0.10488873 0.09425238 0.09438875 0.10658035
  0.10846803 0.09849961 0.09032664 0.09967642]
 [0.1011766  0.09661777 0.09154918 0.11019712 0.09779456 0.10588878
  0.09443601 0.10087729 0.08959807 0.11186467]
 [0.10

INFO:tensorflow:global_step/sec: 90.1714
INFO:tensorflow:probabilities = [[0.09130299 0.09619902 0.09129306 0.10624172 0.09462329 0.11231083
  0.09865811 0.12519626 0.09132116 0.0928535 ]
 [0.0844366  0.09375955 0.09915854 0.11090493 0.09696011 0.12721834
  0.09815827 0.09871212 0.08684468 0.10384689]
 [0.09800351 0.1129735  0.08777978 0.10650075 0.09950869 0.09933347
  0.09359591 0.09910097 0.08927347 0.11392993]
 [0.09708009 0.10686404 0.0981719  0.10488063 0.090285   0.10327759
  0.10517798 0.09434602 0.09900244 0.10091431]
 [0.09706545 0.10556673 0.1010097  0.1040917  0.0944436  0.09949819
  0.10495848 0.09895365 0.09221333 0.10219914]
 [0.09368059 0.10552363 0.10042633 0.11846201 0.09477427 0.09634841
  0.09956374 0.10087484 0.10116582 0.08918038]
 [0.10083886 0.09982961 0.10821357 0.12002565 0.09368119 0.10120807
  0.09067173 0.09698381 0.08890229 0.09964514]
 [0.09787752 0.10966345 0.09736381 0.10859828 0.09904297 0.09773386
  0.09698042 0.10178111 0.08238196 0.10857663]
 [0.098

INFO:tensorflow:loss = 2.2858794, step = 101 (1.121 sec)
INFO:tensorflow:probabilities = [[0.09259937 0.10353477 0.10184175 0.11212859 0.09663488 0.09759852
  0.07550849 0.12166525 0.08374348 0.11474485]
 [0.10195271 0.10190949 0.09593266 0.11224178 0.09072994 0.10091295
  0.09782197 0.10510425 0.08878453 0.10460977]
 [0.09353771 0.09384942 0.10163411 0.11146588 0.09677505 0.09663066
  0.09616707 0.10777403 0.09092394 0.11124216]
 [0.09884777 0.09565137 0.09726787 0.11779218 0.08142584 0.1138583
  0.10974013 0.09682489 0.09745305 0.09113866]
 [0.10113728 0.1015468  0.09889068 0.11113282 0.09826405 0.09370349
  0.10463839 0.093193   0.09834149 0.09915198]
 [0.10438181 0.10699938 0.09801911 0.10029189 0.09936616 0.09689329
  0.09158652 0.10454148 0.10427237 0.09364791]
 [0.09195302 0.11293316 0.09703194 0.1041909  0.09455305 0.101888
  0.09763169 0.09796708 0.09687608 0.10497513]
 [0.09634846 0.10274167 0.09808777 0.1186779  0.09378223 0.09000643
  0.09149711 0.10988376 0.09528708 0.1036

INFO:tensorflow:global_step/sec: 90.4929
INFO:tensorflow:probabilities = [[0.10294288 0.10652041 0.09750592 0.10383719 0.11078499 0.09284091
  0.09271703 0.09549329 0.10112251 0.09623481]
 [0.10213903 0.10154186 0.08756129 0.09729347 0.10005729 0.1006817
  0.09229509 0.10705936 0.09651016 0.11486075]
 [0.10376851 0.11131679 0.09622966 0.0973266  0.09440062 0.09673224
  0.1020225  0.09102123 0.09934284 0.10783903]
 [0.09999261 0.1152803  0.10371087 0.11341761 0.07980571 0.08209968
  0.0923834  0.11252495 0.09355593 0.10722899]
 [0.08591307 0.10314613 0.09393097 0.09768282 0.09232939 0.10529656
  0.10934328 0.11888915 0.08517821 0.10829043]
 [0.09936843 0.1061993  0.10959087 0.1112113  0.08764932 0.10034549
  0.09898224 0.09319559 0.09247681 0.10098072]
 [0.09988935 0.09528358 0.11351721 0.12437758 0.07901769 0.10370559
  0.09307868 0.10212953 0.09205641 0.09694435]
 [0.09871117 0.10544563 0.0815786  0.10909615 0.09211183 0.09485958
  0.11046489 0.10100142 0.09512927 0.11160149]
 [0.0959

...

INFO:tensorflow:global_step/sec: 115.076
INFO:tensorflow:probabilities = [[0.99998355 0.00000005 0.0000061  0.00000012 0.00000001 0.00000431
  0.00000081 0.00000034 0.00000158 0.00000321]
 [0.00028359 0.00034188 0.00416932 0.01291738 0.00224982 0.02202906
  0.00000179 0.04269919 0.1445132  0.77079475]
 [0.00000068 0.000001   0.00001602 0.00172972 0.00000564 0.9935822
  0.00006609 0.         0.00447798 0.00012057]
 [0.0000015  0.00000459 0.00000098 0.00397185 0.00075401 0.00013074
  0.00000015 0.01034904 0.00001965 0.9847675 ]
 [0.00005753 0.00000264 0.00003581 0.0001807  0.00000004 0.999686
  0.00000735 0.00000002 0.00002903 0.00000087]
 [0.00000495 0.00063208 0.00053578 0.00026458 0.8922474  0.00151226
  0.00005311 0.00499407 0.09325942 0.0064963 ]
 [0.         0.00000014 0.00000077 0.00000004 0.9999738  0.00000082
  0.00000277 0.00000104 0.00000007 0.00002052]
 [0.00278556 0.00017526 0.00004962 0.00215299 0.00002776 0.991852
  0.00072916 0.0002946  0.00184096 0.00009206]
 [0.0000031 

INFO:tensorflow:loss = 0.07564766, step = 19801 (0.873 sec)
INFO:tensorflow:probabilities = [[0.00343537 0.00022323 0.0005239  0.04372589 0.00000065 0.9492076
  0.00065065 0.00000496 0.00119615 0.00103147]
 [0.00001125 0.00000084 0.00000986 0.00010284 0.00001308 0.99747187
  0.00023385 0.00000031 0.00215535 0.00000082]
 [0.99948466 0.00000007 0.00000305 0.00000035 0.00000005 0.00004074
  0.0004545  0.00000132 0.00000037 0.00001475]
 [0.00003317 0.01989715 0.02020047 0.00352284 0.07075451 0.00420827
  0.01020125 0.40534398 0.34158728 0.12425122]
 [0.00000011 0.99611545 0.0002692  0.00244863 0.0001274  0.00004131
  0.00000203 0.00016805 0.0008097  0.00001814]
 [0.0000454  0.9713458  0.00107629 0.00655104 0.0009206  0.00058136
  0.00078286 0.00048485 0.01799261 0.00021922]
 [0.00000036 0.00053978 0.9936481  0.00474671 0.00044437 0.00000721
  0.00000472 0.00000804 0.00059745 0.00000319]
 [0.00053325 0.94457585 0.00471361 0.017167   0.00348107 0.00137929
  0.00125387 0.01059639 0.01227767 0

INFO:tensorflow:global_step/sec: 115.361
INFO:tensorflow:probabilities = [[0.00045899 0.00198274 0.00006936 0.00000921 0.00009171 0.02692441
  0.96896356 0.0000012  0.0014983  0.00000057]
 [0.00000081 0.00000695 0.00001481 0.00000024 0.00042242 0.00000467
  0.9994454  0.         0.00010459 0.0000001 ]
 [0.         0.         0.00000159 0.         0.00000016 0.00000142
  0.9999969  0.         0.00000005 0.        ]
 [0.00000427 0.00015162 0.00243404 0.97711426 0.00001821 0.0049707
  0.00000158 0.00002471 0.01508132 0.0001994 ]
 [0.00000085 0.99900705 0.000024   0.00006172 0.00001027 0.00000892
  0.0000224  0.00000361 0.00082688 0.00003432]
 [0.00000007 0.00000082 0.9999677  0.0000293  0.00000001 0.00000078
  0.00000098 0.         0.00000038 0.        ]
 [0.0000002  0.00000002 0.00011244 0.00003246 0.00000039 0.00000059
  0.00000001 0.0000006  0.9998504  0.00000281]
 [0.998741   0.00000002 0.00000998 0.         0.00000531 0.00001438
  0.00122179 0.00000005 0.0000026  0.00000493]
 [0.0000

INFO:tensorflow:loss = 0.042188287, step = 19901 (0.865 sec)
INFO:tensorflow:probabilities = [[0.9841374  0.00000132 0.00020345 0.00007244 0.00000236 0.00432051
  0.00022825 0.00000765 0.0109355  0.00009112]
 [0.00000133 0.00008144 0.00012859 0.00000729 0.99369687 0.00007217
  0.0036932  0.00001066 0.00149646 0.000812  ]
 [0.00000118 0.00000887 0.00001003 0.9996935  0.00000642 0.00009772
  0.00000027 0.00000131 0.00007878 0.00010201]
 [0.00000126 0.00000934 0.00124526 0.00363825 0.00000781 0.00009568
  0.00000004 0.00174871 0.99292266 0.00033093]
 [0.00000077 0.00001846 0.00003709 0.00156957 0.01087499 0.00214891
  0.00000121 0.00129517 0.00077118 0.9832827 ]
 [0.00011448 0.00000002 0.00000976 0.00020375 0.00529456 0.0006404
  0.00000649 0.00017924 0.00015967 0.99339175]
 [0.00001417 0.00000374 0.00000713 0.9981383  0.00000002 0.00046132
  0.00000001 0.00000419 0.00121226 0.00015868]
 [0.00000241 0.00974457 0.03959201 0.8587016  0.00003974 0.00012407
  0.00000063 0.09033699 0.00136967 

INFO:tensorflow:Saving checkpoints for 20000 into /tmp/mnist_convnet_model/model.ckpt.
INFO:tensorflow:Loss for final step: 0.14138885.


In [20]:
eval_input_fn = tf.estimator.inputs.numpy_input_fn(
    x={"x": eval_data},
    y=eval_labels,
    num_epochs=1,
    shuffle=False)
eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
print(eval_results)

INFO:tensorflow:Starting evaluation at 2018-03-12-15:09:52
INFO:tensorflow:Restoring parameters from /tmp/mnist_convnet_model/model.ckpt-20000
INFO:tensorflow:Finished evaluation at 2018-03-12-15:09:53
INFO:tensorflow:Saving dict for global step 20000: accuracy = 0.9718, global_step = 20000, loss = 0.09464826
{'accuracy': 0.9718, 'loss': 0.09464826, 'global_step': 20000}
